# Meander generator using shapely

## Init

In [1]:
import shapely as sp
from shapely.geometry import Point, Polygon, LineString, MultiLineString, MultiPolygon, GeometryCollection
from shapely.ops import linemerge, unary_union

import numpy as np

from IPython.display import display, SVG
from lxml import etree

from matplotlib import pyplot as plt
%matplotlib notebook

## Display

### SVG

In [2]:
def generate_svg_grid( x, y, w, h, d, D, dattrib={}, Dattrib={} ):
    """
    Generates SVG grid pattern
    
    x, y: coordinates to center grid on
    w, h: width and height of grid
    d, D: step size of minor/major grid
    dattrib, Dattrib: attributes to pass to minor/major grid
    """
    
    grid_svg = etree.XML(f"""
    <g>
        <defs>
            <pattern id="smallGrid" width="{d}" height="{d}" patternUnits="userSpaceOnUse">
                <path id="minorSquare" d="M {d} 0 L 0 0 0 {d}" fill="none" stroke="gray" stroke-width="0.05"/>
            </pattern>
            <pattern id="grid" width="{D}" height="{D}" patternUnits="userSpaceOnUse">
                <rect width="{D}" height="{D}" fill="url(#smallGrid)"/>
                <path id="majorSquare" d="M {D} 0 L 0 0 0 {D}" fill="none" stroke="blue" stroke-width=".1"/>
            </pattern>
        </defs>
        <rect x="{x}" y="{y}" width="{w}" height="{h}" fill="url(#grid)" />
    </g>
    """)
    for k in dattrib.keys():
        grid_svg.xpath("//path[@id='minorSquare']")[0].attrib[k] = dattrib[k]
    for k in Dattrib.keys():
        grid_svg.xpath("//path[@id='majorSquare']")[0].attrib[k] = Dattrib[k]
    return( grid_svg )

In [3]:
def nice_svg( e, attribs={"stroke-width":"0"} ):
    """
    Create nice svg path from shapely element e.
    
    attribs: attributes to be overvriten/given
    """
    
    svg = etree.XML( e.svg() )
    for k in attribs.keys():
        svg.attrib[k] = attribs[k]
    return( svg )

In [4]:
def display_svg( elements, bounds ):
    """
    Display collection as an SVG
    """
    
    x1,y1,x2,y2 = bounds
    svg_root = etree.XML(f"""
    <svg viewbox='{x1} {y1} {x2-x1} {y2-y1}' >
    </svg>
    """)
    for e in elements:
        svg_root.append( e )
    display(SVG(etree.tostring(svg_root)))
    

### Matplotlib

In [5]:
def shapely_display_poly( poly, ax, fillkwargs={}, dotkwargs={} ):
    assert( type(poly) == Polygon )
    x, y = poly.exterior.xy
    ax.fill( x, y, **fillkwargs )
    ax.plot(x,y,".",**dotkwargs)

def shapely_display_line( line, ax, pltkwargs={} ):
    assert( type(line) == LineString )
    x, y = line.xy
    ax.plot(x,y,".-",**pltkwargs)

def shapely_display_multiline( mline, ax, pltkwargs={}):
    for line in mline:
        shapely_display_line( line, ax, pltkwargs )

## Shape generators

In [6]:
def circle_segment( P, r, a1=0, a2=np.pi, d=10 ):
    """
    Generate cricle segment
    
    P: center of circel
    r: radius
    a1, a2: start/stop angles
    d: number of segments
    """
    angles = np.linspace( a1, a2, d )
    x = np.sin( angles )*r + P.x
    y = np.cos( angles )*r + P.y
    return( zip( x, y ) )

def box( p, a, b ):
    """
    Draw a box
    
    a: width
    b: height
    """

    return( Polygon([
        [p.x-a/2,p.y-b/2],
        [p.x-a/2,p.y+b/2],
        [p.x+a/2,p.y+b/2],
        [p.x+a/2,p.y-b/2],
    ]))


def square( p, a ):
    """
    Draw square
    
    p: center of square
    a: side length
    """
    
    return( box(p,a,a) )

def basic_meander_line( l, r, n, d=10 ):
    """
    Very basic meander line
    
    l: length of straight lines
    r: radius bends
    n: straights total
    """
    lines = [ [[0,i*2*r],[l,i*2*r]][::(1-i%2*2)] for i in range(n) ]
    circles = [ circle_segment(
            Point([l*((i+1)%2),(i*2+1)*r]),
            r,
            np.pi*(1-i%2*2),
            0,
            d=d) for i in range(n-1) ]
    meander = []
    for i in range(n-1):
        meander.extend( lines[i] )
        meander.extend( circles[i] )
    meander.extend( lines[n-1] )
    return( LineString(meander) )

def line_to_cpwg( l, s, w ):
    """
    Generate two ditches of CPWG along the given line(s)
    
    s, w: CPWG parameters
    """

    left_line = line.parallel_offset( (s+w)/2, "left", resolution=1 )
    right_line = line.parallel_offset( (s+w)/2, "right", resolution=1 )
    left_ditch = left_line.buffer( w/2, cap_style=2, resolution=1, )
    right_ditch = right_line.buffer( w/2, cap_style=2, resolution=1 )
    return( (left_ditch, right_ditch, line, left_line, right_line) )
    
def basic_meander( l, r, n, s, w, d=10 ):
    """
    Very basic meander CPWG
    Can't use line_to_cpwg, strange bug with parallel_offset
    
    s, w: CPWG parameters
    l: length of straight lines
    r: radius bends
    n: straights total
    """
    
    line = basic_meander_line( l, r, n, d )
    left_line = line.parallel_offset( (s+w)/2, "left", resolution=1 )
    right_line = line.parallel_offset( (s+w)/2, "right", resolution=1 )
    if n%2 == 0: # wierd shapely bug
        right_line = LineString( right_line.coords[1:-1] ) #
    left_ditch = left_line.buffer( w/2, cap_style=2, resolution=1, )
    right_ditch = right_line.buffer( w/2, cap_style=2, resolution=1 )
    return( (left_ditch, right_ditch, line, left_line, right_line) )

### Launcher

In [7]:
def launcher( s, w, a, b, c, g ):
    """
    Generate rectangular launcher
    
    s, w: CPWG parameters of line to connect to
    a, b: width, height of launcher
    c: lengt of transitional triangle
    g: gap around launcher 
    """
    
    outer_launcher = box( Point(c+a/2+g/2,0), a+g, b+2*g )
    inner_launcher = box( Point(c+a/2,0), a, b )
    outer_trans = Polygon( [[0,s/2+w],[c,b/2+g],[c,-b/2-g],[0,-s/2-w]])
    inner_trans = Polygon( [[0,s/2],[c,b/2],[c,-b/2],[0,-s/2]])
    inside = unary_union( [inner_trans, inner_launcher] )
    outside = unary_union( [outer_trans, outer_launcher] )
    launcher = outside.difference( inside )
    return( launcher, inside, outside )

### Simple meander test

In [8]:
l,r,m,ll,rl = basic_meander( 6, 1.5, 5, .3, .3, 20 )
launch, ins, out = launcher(.3, .3, 6, 5, 3, 1.5)
launch = sp.affinity.rotate( launch, angle=180, origin=(0,0) )
display_svg(
    (
        nice_svg(l,attribs={"fill":"#00ff00", "fill-opacity":"1", "stroke-width":"0"}),
        nice_svg(r,attribs={"fill":"#ff0000", "fill-opacity":"1", "stroke-width":"0"}),
        nice_svg(launch,attribs={"fill":"#ffaaff", "fill-opacity":"1", "stroke-width":"0"}),
        nice_svg(m,attribs={"stroke-width":".1"}),
        nice_svg(rl,attribs={"stroke-width":".1"}),
        nice_svg(ll,attribs={"stroke-width":".1"}),
        
        generate_svg_grid(-3,-3,30,30,.3,3)
    ),
    m.union(launch).buffer(1).bounds
)

## Patterning

In [10]:
def generate_dots_sq( r, d, bounding_box ):
    """
    Generate square lattice of round dots
    
    r: radius of single dot
    d: distance of dots
    bounding_box: x1,y1,x2,y2 of box to generate dots in
    """
    
    x1,y1,x2,y2 = bounding_box
    nx = (x2-x1)/d
    ny = (y2-y1)/d
    dots = []
    for x in range( int(nx)+1 ):
        for y in range( int(ny)+1 ):
            dots.append( Polygon(circle_segment(Point(x*d+x1,y*d+y1),r,a1=0, a2=np.pi*2 ) ) )
    return( dots )

def generate_dots_tri( r, d, bounding_box ):
    """
    Generate hex lattice of round dots
    
    r: radius of single dot
    d: distance of dots
    bounding_box: x1,y1,x2,y2 of box to generate dots in
    """
    
    x1,y1,x2,y2 = bounding_box
    nx = (x2-x1)/d
    ny = (y2-y1)/d*np.sqrt(2)
    dots = []
    for x in range( int(nx)+1 ):
        for y in range( int(ny)+1 ):
            dots.append(Polygon(circle_segment(
                Point((x+y%2/2)*d+x1,y*d/np.sqrt(2)+y1)
                ,r,0,np.pi*2)))
    return( dots )

def generate_squares( a, d, bounding_box ):
    """
    Generate square pattern
    
    a: side length of squares
    d: distance between squares
    bounding_box: x1,y1,x2,y2 bounds of area to generate pattern in
    """
    
    x1,y1,x2,y2 = bounding_box
    nx = (x2-x1)/d
    ny = (y2-y1)/d
    squares = []
    for x in range( int(nx)+1 ):
        for y in range( int(ny)+1 ):
            squares.append( Polygon( square(Point((x+y%2/2)*d+x1,y*d+y1),a)))
    return( squares )

In [13]:
l,r,m,ll,rl = basic_meander( 6, 1.5, 4, .3, .3, 20 )
end_cap = box( Point(0,0), .3, .9 )
near = m.buffer(1)
edges = unary_union( [r, l, end_cap] )
dots = generate_dots_tri( .03, .09, near.bounds )
dots_good = [ d for d in dots if near.contains(d) and edges.distance(d) > .02]
squares = generate_squares( .5, .6, near.buffer(2).bounds )
for i in range(len(squares)):
    squares[i] = squares[i].difference( near.buffer(.05) )
display_svg(
    (
        #nice_svg(l,attribs={"fill":"#77f", "fill-opacity":"1", "stroke-width":"0"}),
        #nice_svg(r,attribs={"fill":"#7f7", "fill-opacity":"1", "stroke-width":"0"}),
        #nice_svg(end_cap,attribs={"fill":"#f77", "fill-opacity":"1", "stroke-width":"0"}),
        nice_svg(edges,attribs={"fill":"#fff", "fill-opacity":".7", "stroke-width":"0"}),
        #nice_svg(m,attribs={"stroke-width":".1"}),
        #generate_svg_grid(-3,-3,30,30,.3,3),
        *[nice_svg(d) for d in dots_good],
        *[nice_svg(sq) for sq in squares],
    ),
    m.buffer(1.2).bounds
)


## DXF output

In [ ]:
def poly_to_dxf( poly, doc ):
    """
    Add a shapely Polygon to the model space of a dxf document
    """
    
    